In [1]:
import pandas as pd
import numpy as np
import re
import csv
import os
# import nltk
from numpy import triu
# nltk.download('words')
# from nltk.corpus import words
from numpy import dot
from numpy.linalg import norm
from gensim.models import Word2Vec
from gensim.models.phrases import Phraser, Phrases

In [2]:
data = pd.read_csv('new_data.csv',on_bad_lines='skip')
data

Salts  \
0                                     amitriptyline 25 mg   
1                                  Amitriptyline(25.0 Mg)   
2                        Amitriptyline + Chlordiazepoxide   
3         Amitriptyline (12.5mg) + Chlordiazepoxide (5mg)   
4                                  Amitriptyline(10.0 Mg)   
...                                                   ...   
517008                                 Cefuroxime (500mg)   
517009       Cefuroxime (500mg) + Clavulanic Acid (125mg)   
517010                                 Telmisartan (40mg)   
517011                                  Deflazacort (6mg)   
517012  Ambroxol (15mg/5ml) + Guaifenesin (50mg/5ml) +...   

                         Medicine_Name  
0             amilift 25 sr tablet 10s  
1              amilift sr 25mg tablets  
2                   amilift dx tablets  
3       amilift dx 12.5 mg 5 mg tablet  
4                 amilift 10mg tablets  
...                                ...  
517008           zeoroxim 500mg tablet  
517009  zeoroxim cv 500mg 125mg tablet  
517010              zicard 40mg tablet  
517011                zofla 6mg tablet  
517012                   zifo at syrup  

[517013 rows x 2 columns]

In [3]:
# filtered_data = data[data['Salts'].str.contains('Paracetamol', case=False, na=False)]
filtered_data = data.iloc[:,:]

In [4]:
filtered_data

Salts  \
0                                     amitriptyline 25 mg   
1                                  Amitriptyline(25.0 Mg)   
2                        Amitriptyline + Chlordiazepoxide   
3         Amitriptyline (12.5mg) + Chlordiazepoxide (5mg)   
4                                  Amitriptyline(10.0 Mg)   
...                                                   ...   
517008                                 Cefuroxime (500mg)   
517009       Cefuroxime (500mg) + Clavulanic Acid (125mg)   
517010                                 Telmisartan (40mg)   
517011                                  Deflazacort (6mg)   
517012  Ambroxol (15mg/5ml) + Guaifenesin (50mg/5ml) +...   

                         Medicine_Name  
0             amilift 25 sr tablet 10s  
1              amilift sr 25mg tablets  
2                   amilift dx tablets  
3       amilift dx 12.5 mg 5 mg tablet  
4                 amilift 10mg tablets  
...                                ...  
517008           zeoroxim 500mg tablet  
517009  zeoroxim cv 500mg 125mg tablet  
517010              zicard 40mg tablet  
517011                zofla 6mg tablet  
517012                   zifo at syrup  

[517013 rows x 2 columns]

In [132]:
filtered_data['Salts'] = filtered_data['Salts'].str.replace('('," ").str.replace(")","").str.replace("-"," ").str.replace("mg"," mg").str.replace("%"," %").str.replace(","," + ")

C:\Users\ayush\AppData\Local\Temp\ipykernel_19732\2205570430.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_data['Salts'] = filtered_data['Salts'].str.replace('('," ").str.replace(")","").str.replace("-"," ").str.replace("mg"," mg").str.replace("%"," %").str.replace(","," + ")


In [133]:
filtered_data['Salts'] = filtered_data['Salts'].str.lower()

C:\Users\ayush\AppData\Local\Temp\ipykernel_19732\1898822662.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_data['Salts'] = filtered_data['Salts'].str.lower()


In [134]:
def convert_integer_to_float(value):
    try:
        # Use regex to find the numeric part
        match = re.search(r"(\d+(\.\d+)?)", value)
        if match:
            numeric_part = match.group()
            # Check if the numeric part is an integer
            if numeric_part.isdigit():
                numeric_part = float(numeric_part)
                # Replace the integer part with its float representation
                value = re.sub(r"\d+", str(numeric_part), value, 1)
        return value
    except:
        return value

In [135]:
filtered_data['Salts']= filtered_data['Salts'].str.replace(r'^\s+|\s+$', '', regex=True).apply(convert_integer_to_float)

C:\Users\ayush\AppData\Local\Temp\ipykernel_19732\4241115467.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_data['Salts']= filtered_data['Salts'].str.replace(r'^\s+|\s+$', '', regex=True).apply(convert_integer_to_float)


In [136]:
filtered_data['Salts'] = filtered_data['Salts'].str.strip().str.replace('mcg',' mcg').str.replace("mg"," mg").str.replace("ml","  ml").str.replace("w/w","").str.replace("   "," ").str.replace("  "," ").str.replace('% ','%')

C:\Users\ayush\AppData\Local\Temp\ipykernel_19732\4002121545.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_data['Salts'] = filtered_data['Salts'].str.strip().str.replace('mcg',' mcg').str.replace("mg"," mg").str.replace("ml","  ml").str.replace("w/w","").str.replace("   "," ").str.replace("  "," ").str.replace('% ','%')


In [137]:
filtered_data

Salts                 Medicine_Name
500                           losartan 25.0 mg         angilos 25 tablet 10s
501                           losartan 25.0 mg          angilos 25mg tablets
502                           losartan 50.0 mg     angilos 50 mg tablet 10's
503        losartan 50.0 mg + a mlodipine 5 mg    angilos am 50mg 5mg tablet
504        a mlodipine 5.0 mg + losartan 50 mg         angilos am tablet 10s
...                                        ...                           ...
1495   adapalene 0.1 %+ benzoyl peroxide 2.5 %    adabor 0.1/2.5 % gel 15 gm
1496   adapalene 0.1 %+ benzoyl peroxide 2.5 %  adabor gel tube of 15 gm gel
1497  adapalene 0.1 %+ benzoyl peroxide 0.25 %               adabor gel 15gm
1498   adapalene 0.1 %+ benzoyl peroxide 2.5 %                    adabor gel
1499   adapalene 0.1 %+ benzoyl peroxide 2.5 %              adabor gel 15 gm

[1000 rows x 2 columns]

In [138]:
new_df = filtered_data.drop_duplicates(subset='Salts')

In [139]:
new_df = new_df.reset_index(drop=True)
new_df

Salts  \
0                                     losartan 25.0 mg   
1                                     losartan 50.0 mg   
2                  losartan 50.0 mg + a mlodipine 5 mg   
3                  a mlodipine 5.0 mg + losartan 50 mg   
4                               a mlodipine + losartan   
..                                                 ...   
543  clopidogrel 75.0 mg + aspirin / acetyl salicyl...   
544  aspirin/acetylsalicylic acid 75.0 mg + clopido...   
545                aspirin 75.0 mg + clopidogrel 75 mg   
546            adapalene 0.1 %+ benzoyl peroxide 2.5 %   
547           adapalene 0.1 %+ benzoyl peroxide 0.25 %   

                                         Medicine_Name  
0                                angilos 25 tablet 10s  
1                            angilos 50 mg tablet 10's  
2                           angilos am 50mg 5mg tablet  
3                                angilos am tablet 10s  
4                                   angilos am tablets  
..                                                 ...  
543           antiplatt plus 150mg strip of 10 tablets  
544  antiplatt plus 75 mg/75 mg tablet strip of 10 ...  
545                         antiplatt plus 75mg tablet  
546                         adabor 0.1/2.5 % gel 15 gm  
547                                    adabor gel 15gm  

[548 rows x 2 columns]

In [140]:
raw_salts = list(new_df.Salts)

In [141]:
#sentences contain all the salts without their compositions
sentences = []
for i in range(0, len(raw_salts)):
    sentences.append(list(filter(None, re.sub("[^a-zA-Z.]", " ", raw_salts[i]).split(' ')))) 
all_salts = [x for x in sentences ]

In [142]:
#dosages or compositions associated with each salt
dosages = []
for i in range(0, len(raw_salts)):
    dosages.append(list(filter(None, re.sub("[^0-9.]", " ", raw_salts[i]).split(' ')))) 
compositions = [x for x in dosages ]

In [143]:
for i in range(0, len(all_salts)):
    all_salts[i] = [x.lower() for x in all_salts[i]]

In [144]:
#salt cleaning
all_salts = [[word for word in salt if len(word) > 3] for salt in all_salts]
words_to_remove = {'billion','undefinedundefined','Check', 'more', 'medicines', 'with', 'composition', 'as','check','gm','spores','million','product','mcg','mg','ml','Ml','salt','iu','nutritional'}
all_salts = [[word for word in sublist if word not in words_to_remove] for sublist in all_salts]
all_salts = [sublist for sublist in all_salts if len(sublist)>0]

In [145]:
def is_float(value):
    try:
        float_value = float(value)
        return True
    except ValueError:
        return False
compositions = [[x for x in lst if is_float(x)] for lst in compositions]


In [146]:
compositions = [[x for x in lst] for lst in compositions if len(lst) >0]
compositions = set([float(x)  for lst in compositions for x in lst])

In [147]:
num_dict = {value: [value/1000, value/1000, value/1000] for value in compositions}

In [148]:
num_dict

{0.75: [0.00075, 0.00075, 0.00075],
 1.0: [0.001, 0.001, 0.001],
 2.0: [0.002, 0.002, 0.002],
 3.0: [0.003, 0.003, 0.003],
 4.0: [0.004, 0.004, 0.004],
 5.0: [0.005, 0.005, 0.005],
 2.5: [0.0025, 0.0025, 0.0025],
 7.0: [0.007, 0.007, 0.007],
 8.0: [0.008, 0.008, 0.008],
 9.0: [0.009, 0.009, 0.009],
 10.0: [0.01, 0.01, 0.01],
 0.5: [0.0005, 0.0005, 0.0005],
 12.5: [0.0125, 0.0125, 0.0125],
 12.0: [0.012, 0.012, 0.012],
 10.2: [0.010199999999999999, 0.010199999999999999, 0.010199999999999999],
 15.0: [0.015, 0.015, 0.015],
 13.2: [0.0132, 0.0132, 0.0132],
 20.0: [0.02, 0.02, 0.02],
 25.0: [0.025, 0.025, 0.025],
 27.5: [0.0275, 0.0275, 0.0275],
 28.5: [0.0285, 0.0285, 0.0285],
 30.0: [0.03, 0.03, 0.03],
 0.25: [0.00025, 0.00025, 0.00025],
 6.0: [0.006, 0.006, 0.006],
 1.5: [0.0015, 0.0015, 0.0015],
 1.25: [0.00125, 0.00125, 0.00125],
 35.0: [0.035, 0.035, 0.035],
 6.5: [0.0065, 0.0065, 0.0065],
 7.5: [0.0075, 0.0075, 0.0075],
 38.0: [0.038, 0.038, 0.038],
 6.25: [0.00625, 0.00625, 0.00625

In [149]:
all_salts

[['losartan'],
 ['losartan'],
 ['losartan', 'mlodipine'],
 ['mlodipine', 'losartan'],
 ['mlodipine', 'losartan'],
 ['hydrochlorothiazide', 'losartan'],
 ['hydrochlorothiazide', 'losartan'],
 ['losartan'],
 ['cefuroxime', 'clavulanic', 'acid'],
 ['cefuroxime'],
 ['aceclofenac', 'paracetamol', 'acetaminophen'],
 ['aceclofenac', 'serratiopeptidase'],
 ['aceclofenac', 'paracetamol', 'serratiopeptidase'],
 ['aceclofenac', 'chlorzoxazone', 'paracetamol'],
 ['aceclofenac', 'chlorzoxazone', 'paracetamol'],
 ['aceclofenac', 'serratiopeptidase'],
 ['aceclofenac', 'paracetamol'],
 ['aceclofenac', 'paracetamol', 'acetaminophen'],
 ['aceclofenac', 'paracetamol', 'serratiopeptidase'],
 ['aceclofenac'],
 ['aceclofenac', 'thiocolchicoside'],
 ['aceclofenac', 'thiocolchicoside'],
 ['aceclofenac', 'paracetamol', 'chlorzoxazone'],
 ['permethrin'],
 ['permethrin'],
 ['acetazolamide'],
 ['rosuvastatin', 'fenofibrate'],
 ['ferrous',
  'ascorbate',
  'folic',
  'acid',
  'methylcobalamin',
  'vitamin',
  'vi

In [150]:
#Model for the embeddings 
model = Word2Vec(all_salts, vector_size=512, min_count=1, window=3, compute_loss=True, shrink_windows=True)

In [151]:
model.wv.most_similar('paracetamol', topn=10)

[('clavulanic', 0.12497396767139435),
 ('sulfate', 0.12154833972454071),
 ('omega', 0.11726409941911697),
 ('methylprednisolone', 0.11240091174840927),
 ('multiminerals', 0.10429752618074417),
 ('mannose', 0.10412846505641937),
 ('methylcellulose', 0.10034383833408356),
 ('maleate', 0.09629057347774506),
 ('leucine', 0.09326335787773132),
 ('methylcobalamin', 0.0833946093916893)]

In [152]:
model.wv.index_to_key

['vitamin',
 'acid',
 'paracetamol',
 'aceclofenac',
 'mlodipine',
 'zinc',
 'methylcobalamin',
 'telmisartan',
 'folic',
 'serratiopeptidase',
 'ofloxacin',
 'cefixime',
 'citrate',
 'calcium',
 'pyridoxine',
 'amoxycillin',
 'montelukast',
 'azithromycin',
 'mecobalamin',
 'domperidone',
 'atorvastatin',
 'metoprolol',
 'cyproheptadine',
 'magnesium',
 'sodium',
 'diclofenac',
 'acebrophylline',
 'clavulanic',
 'cynocobalamin',
 'alpha',
 'elemental',
 'chloride',
 'aspirin',
 'chlorthalidone',
 'ornidazole',
 'ambroxol',
 'potassium',
 'cefpodoxime',
 'fexofenadine',
 'methyl',
 'losartan',
 'cholecalciferol',
 'levofloxacin',
 'acetaminophen',
 'thiocolchicoside',
 'ferrous',
 'beta',
 'pregabalin',
 'clopidogrel',
 'gluconate',
 'ascorbic',
 'thiamine',
 'biotin',
 'maleate',
 'arginine',
 'sulphate',
 'rabeprazole',
 'riboflavin',
 'lipoic',
 'niacinamide',
 'hydrogen',
 'ascorbate',
 'disodium',
 'copper',
 'acetyl',
 'guaifenesin',
 'menthol',
 'ampicillin',
 'iron',
 'terbinaf

In [153]:
high_dim_embeds = np.asarray(model.wv.vectors)
words_arr = list(np.asarray(model.wv.index_to_key))
words_list = list(words_arr)

In [154]:
words_arr

['vitamin',
 'acid',
 'paracetamol',
 'aceclofenac',
 'mlodipine',
 'zinc',
 'methylcobalamin',
 'telmisartan',
 'folic',
 'serratiopeptidase',
 'ofloxacin',
 'cefixime',
 'citrate',
 'calcium',
 'pyridoxine',
 'amoxycillin',
 'montelukast',
 'azithromycin',
 'mecobalamin',
 'domperidone',
 'atorvastatin',
 'metoprolol',
 'cyproheptadine',
 'magnesium',
 'sodium',
 'diclofenac',
 'acebrophylline',
 'clavulanic',
 'cynocobalamin',
 'alpha',
 'elemental',
 'chloride',
 'aspirin',
 'chlorthalidone',
 'ornidazole',
 'ambroxol',
 'potassium',
 'cefpodoxime',
 'fexofenadine',
 'methyl',
 'losartan',
 'cholecalciferol',
 'levofloxacin',
 'acetaminophen',
 'thiocolchicoside',
 'ferrous',
 'beta',
 'pregabalin',
 'clopidogrel',
 'gluconate',
 'ascorbic',
 'thiamine',
 'biotin',
 'maleate',
 'arginine',
 'sulphate',
 'rabeprazole',
 'riboflavin',
 'lipoic',
 'niacinamide',
 'hydrogen',
 'ascorbate',
 'disodium',
 'copper',
 'acetyl',
 'guaifenesin',
 'menthol',
 'ampicillin',
 'iron',
 'terbinaf

In [155]:
len(high_dim_embeds)

370

In [156]:
words_list

['vitamin',
 'acid',
 'paracetamol',
 'aceclofenac',
 'mlodipine',
 'zinc',
 'methylcobalamin',
 'telmisartan',
 'folic',
 'serratiopeptidase',
 'ofloxacin',
 'cefixime',
 'citrate',
 'calcium',
 'pyridoxine',
 'amoxycillin',
 'montelukast',
 'azithromycin',
 'mecobalamin',
 'domperidone',
 'atorvastatin',
 'metoprolol',
 'cyproheptadine',
 'magnesium',
 'sodium',
 'diclofenac',
 'acebrophylline',
 'clavulanic',
 'cynocobalamin',
 'alpha',
 'elemental',
 'chloride',
 'aspirin',
 'chlorthalidone',
 'ornidazole',
 'ambroxol',
 'potassium',
 'cefpodoxime',
 'fexofenadine',
 'methyl',
 'losartan',
 'cholecalciferol',
 'levofloxacin',
 'acetaminophen',
 'thiocolchicoside',
 'ferrous',
 'beta',
 'pregabalin',
 'clopidogrel',
 'gluconate',
 'ascorbic',
 'thiamine',
 'biotin',
 'maleate',
 'arginine',
 'sulphate',
 'rabeprazole',
 'riboflavin',
 'lipoic',
 'niacinamide',
 'hydrogen',
 'ascorbate',
 'disodium',
 'copper',
 'acetyl',
 'guaifenesin',
 'menthol',
 'ampicillin',
 'iron',
 'terbinaf

In [157]:
high_dim_embeds

array([[-7.2397517e-05, -9.9336336e-05,  9.7130990e-04, ...,
        -1.5003718e-03, -1.2608585e-03, -5.3872506e-04],
       [-1.3696540e-03, -2.0117988e-03, -5.5375468e-04, ...,
        -6.0233672e-04,  1.2373636e-03, -7.4086816e-04],
       [-1.2808881e-03,  7.9576619e-04, -1.0862258e-04, ...,
         1.8094628e-03, -1.2186930e-03,  1.5951761e-03],
       ...,
       [ 5.7108887e-04,  1.8072384e-03, -1.7721802e-03, ...,
        -1.9530961e-03, -1.2456055e-03, -6.1417255e-04],
       [ 2.4727918e-04, -9.7432407e-04, -1.6288527e-03, ...,
         9.5808459e-04, -4.3754862e-04, -3.1702686e-05],
       [ 6.9349844e-05,  9.3574071e-04, -9.5955300e-05, ...,
        -1.5352899e-03,  2.9110847e-04, -1.7920218e-04]], dtype=float32)

In [158]:
word_vector_mapping = list(zip(words_list, high_dim_embeds))

In [159]:
word_vector_mapping[2]

('paracetamol',
 array([-1.2808881e-03,  7.9576619e-04, -1.0862258e-04, -6.7449332e-04,
         1.3728560e-03,  7.9856830e-04, -7.4911729e-04,  1.4737216e-04,
         1.7790616e-03,  1.5171325e-03,  1.2610605e-03,  8.8842411e-04,
         4.8442732e-04, -4.0028620e-04, -1.2554443e-03, -2.6578797e-05,
        -2.8699869e-04, -6.4196553e-05, -1.2494577e-03,  1.4569489e-03,
        -1.2482214e-03, -1.4295204e-03, -5.0776545e-04, -2.7935451e-04,
        -1.5416072e-03,  1.1817152e-04, -1.0434836e-03, -2.5015505e-04,
        -1.3929892e-03,  3.7333087e-04,  6.5554556e-04, -4.5164332e-05,
        -1.0499243e-03, -3.3834449e-04,  1.3689261e-03,  8.0160983e-04,
        -1.7085535e-03, -6.9562707e-04,  4.2771181e-04,  3.9914806e-04,
        -1.8400804e-03,  8.8593969e-04, -1.7351673e-03, -1.5088599e-03,
         7.1300869e-04, -7.0090260e-04,  7.3516462e-04,  1.7413207e-03,
        -6.4317312e-04,  1.8304940e-03,  3.1992851e-04,  1.9454018e-03,
         1.1711254e-03, -1.7826983e-03, -7.69062

In [160]:
word_vectors = {word: vector for word, vector in word_vector_mapping}
# Get vectors for words in each list
list_vectors = [[word_vectors[word] for word in word_list] for word_list in all_salts]
# Display the result
resultant_vectors = [np.sum(np.array(vectors)/512, axis=0) for vectors in list_vectors]

In [161]:
resultant_vectors

[array([ 3.70937460e-06,  8.84809481e-07,  2.82681413e-06,  2.49755021e-06,
         1.17893805e-07,  5.67995187e-07, -3.21515881e-06, -8.00246426e-07,
        -2.74897479e-06,  6.38027700e-07, -8.23968833e-07,  3.09377356e-06,
        -3.12905831e-06, -2.21943537e-06, -1.39726933e-06, -5.55698193e-07,
        -2.04324783e-06,  1.56625174e-06, -1.70983697e-06, -6.32878283e-08,
        -2.26427730e-07, -3.60655486e-06,  2.45962178e-06, -1.46431546e-06,
        -3.16023215e-06, -8.56920678e-07, -1.73875981e-06,  1.68178119e-07,
         1.72547766e-06, -5.74520641e-07, -4.72904134e-07,  1.51029917e-06,
         9.22855214e-09,  9.30268357e-07, -2.48263677e-06,  1.36992435e-06,
        -1.87236344e-06, -2.40888335e-06,  3.69803251e-06,  3.25628912e-06,
        -2.44008152e-06,  7.44199212e-07, -6.42689599e-07, -1.70271574e-06,
         1.79221354e-06,  3.06451739e-06, -1.25492181e-06,  1.05155186e-06,
        -2.39632209e-06,  3.46970432e-06,  1.05055517e-06, -1.51049477e-07,
         1.6

In [162]:
# Function to check if a string is a valid number
def is_valid_number(num_str):
    return re.match(r'^-?\d+(\.\d+)?$', num_str) is not None

# Process the dosages list
num_list_vectors = [
    [num_dict.get(float(num), [0, 0, 0]) if is_valid_number(num) else [0, 0, 0] for num in num_list]
    for num_list in dosages
]

# Display the result
resultant_num_vectors = [np.sum(np.array(vectors), axis=0) for vectors in num_list_vectors]

In [163]:
# #UMAP for dimentionality reduction
# import umap.umap_ as umap
# reducer = umap.UMAP(
#     n_components=256,
#     n_neighbors=50,
#     n_epochs=2000,
#     min_dist=0.05,
#     local_connectivity=100.0,
#     spread= 0.05
# )
# embedding = reducer.fit_transform(resultant_vectors)

In [164]:
# import umap.umap_ as umap
# no_of_dimensions = [256,128,64,32,16,8,3]
# for i in no_of_dimensions:
#     reducer = umap.UMAP(
#     n_components=i,
#     n_neighbors=50,
#     n_epochs=2000,
#     min_dist=0.05,
#     local_connectivity=100.0,
#     spread= 0.05)
#     embedding = reducer.fit_transform(embedding)
    

In [165]:
np.array(resultant_vectors).shape

(547, 512)

In [184]:
from sklearn.manifold import TSNE
model = TSNE(n_components=256, perplexity=100.0,
              early_exaggeration=10.0,
                learning_rate='auto',
                  n_iter_without_progress=100,
                    min_grad_norm=1e-07,
                      metric='euclidean',
                      metric_params=None, init='pca', verbose=0, random_state=None, method='exact', angle=0.5, n_jobs=None)
embedding = model.fit_transform(np.array(resultant_vectors))

In [185]:
no_of_dimensions = [128,64,32,16,8,3]
for i in no_of_dimensions:
    model = TSNE(n_components=i, perplexity=100.0,
              early_exaggeration=10.0,
                learning_rate='auto',
                  n_iter_without_progress=100,
                    min_grad_norm=1e-07,
                      metric='euclidean',
                      metric_params=None, init='pca', verbose=0, random_state=None, method='exact', angle=0.5, n_jobs=None)
    embedding = model.fit_transform(np.array(embedding))

In [186]:
final_list = list(zip(new_df['Medicine_Name'],new_df['Salts'],embedding,dosages))
final_dataframe = pd.DataFrame(final_list,columns = ['Medicine_Name','Salts','vector','dosage'])

In [187]:
def sum_vectors(numbers):
    try:
        vectors = [[0.001 * float(num), 0.001 * float(num), 0.001 * float(num)] for num in numbers]
        return np.sum(np.array(vectors), axis=0)
    except ValueError:
        return [0, 0, 0]
    except TypeError:  # Handle the case where numbers is an empty list
        return [0, 0, 0]

# Apply the function to the 'your_column' and create a new column 'SumVectors'
final_dataframe['SumVectors'] = final_dataframe['dosage'].apply(sum_vectors)

In [188]:
final_dataframe

Medicine_Name  \
0                                angilos 25 tablet 10s   
1                            angilos 50 mg tablet 10's   
2                           angilos am 50mg 5mg tablet   
3                                angilos am tablet 10s   
4                                   angilos am tablets   
..                                                 ...   
542  antiplatt plus 150 mg/75 mg tablet strip of 10...   
543           antiplatt plus 150mg strip of 10 tablets   
544  antiplatt plus 75 mg/75 mg tablet strip of 10 ...   
545                         antiplatt plus 75mg tablet   
546                         adabor 0.1/2.5 % gel 15 gm   

                                                 Salts  \
0                                     losartan 25.0 mg   
1                                     losartan 50.0 mg   
2                  losartan 50.0 mg + a mlodipine 5 mg   
3                  a mlodipine 5.0 mg + losartan 50 mg   
4                               a mlodipine + losartan   
..                                                 ...   
542  aspirin/acetylsalicylic acid 150.0 mg + clopid...   
543  clopidogrel 75.0 mg + aspirin / acetyl salicyl...   
544  aspirin/acetylsalicylic acid 75.0 mg + clopido...   
545                aspirin 75.0 mg + clopidogrel 75 mg   
546            adapalene 0.1 %+ benzoyl peroxide 2.5 %   

                                  vector         dosage  \
0    [-5.7047486, -1.1721812, 1.3178241]         [25.0]   
1     [-5.513812, -0.9735408, 1.1201787]         [50.0]   
2    [-6.151596, -1.3261145, 0.82413894]      [50.0, 5]   
3    [-6.151596, -1.3261145, 0.82413894]      [5.0, 50]   
4    [-6.151596, -1.3261145, 0.82413894]             []   
..                                   ...            ...   
542    [3.845325, 1.7525554, -1.6686797]    [150.0, 75]   
543    [3.391115, 1.6387248, -1.7444034]  [75.0, 150.0]   
544      [4.05685, 1.7666304, -2.056936]     [75.0, 75]   
545  [-6.041723, -1.7156223, -0.3165637]     [75.0, 75]   
546  [-6.041723, -1.7156223, -0.3165637]     [0.1, 2.5]   

                                            SumVectors  
0                                [0.025, 0.025, 0.025]  
1                                   [0.05, 0.05, 0.05]  
2                                [0.055, 0.055, 0.055]  
3                                [0.055, 0.055, 0.055]  
4                                                  0.0  
..                                                 ...  
542  [0.22499999999999998, 0.22499999999999998, 0.2...  
543  [0.22499999999999998, 0.22499999999999998, 0.2...  
544                                 [0.15, 0.15, 0.15]  
545                                 [0.15, 0.15, 0.15]  
546                           [0.0026, 0.0026, 0.0026]  

[547 rows x 5 columns]

In [189]:
final_dataframe['final_vector'] = final_dataframe['vector'] + final_dataframe['SumVectors']

In [190]:
final_dataframe['Salts'] = final_dataframe['Salts'].str.replace('('," ").str.replace(")","").str.replace("-"," ").str.replace("mg"," mg").str.replace("%"," %").str.replace(","," + ")

In [191]:
final_dataframe['Salts'] = final_dataframe['Salts'].str.lower()

In [192]:
def convert_integer_to_float(value):
    try:
        # Use regex to find the numeric part
        match = re.search(r"(\d+(\.\d+)?)", value)
        if match:
            numeric_part = match.group()
            # Check if the numeric part is an integer
            if numeric_part.isdigit():
                numeric_part = float(numeric_part)
                # Replace the integer part with its float representation
                value = re.sub(r"\d+", str(numeric_part), value, 1)
        return value
    except:
        return value

In [193]:
final_dataframe['Salts']= final_dataframe['Salts'].str.replace(r'^\s+|\s+$', '', regex=True).apply(convert_integer_to_float)

In [194]:
final_dataframe['Salts'] = final_dataframe['Salts'].str.strip().str.replace('mcg',' mcg').str.replace("mg"," mg").str.replace("w/w","").str.replace("   "," ").str.replace("  "," ").str.replace('% ','%')

In [195]:
new_df = final_dataframe.drop_duplicates(subset='Salts')

In [196]:
new_df = new_df.reset_index(drop=True)
new_df

Medicine_Name  \
0                                angilos 25 tablet 10s   
1                            angilos 50 mg tablet 10's   
2                           angilos am 50mg 5mg tablet   
3                                angilos am tablet 10s   
4                                   angilos am tablets   
..                                                 ...   
542  antiplatt plus 150 mg/75 mg tablet strip of 10...   
543           antiplatt plus 150mg strip of 10 tablets   
544  antiplatt plus 75 mg/75 mg tablet strip of 10 ...   
545                         antiplatt plus 75mg tablet   
546                         adabor 0.1/2.5 % gel 15 gm   

                                                 Salts  \
0                                     losartan 25.0 mg   
1                                     losartan 50.0 mg   
2                  losartan 50.0 mg + a mlodipine 5 mg   
3                  a mlodipine 5.0 mg + losartan 50 mg   
4                               a mlodipine + losartan   
..                                                 ...   
542  aspirin/acetylsalicylic acid 150.0 mg + clopid...   
543  clopidogrel 75.0 mg + aspirin / acetyl salicyl...   
544  aspirin/acetylsalicylic acid 75.0 mg + clopido...   
545                aspirin 75.0 mg + clopidogrel 75 mg   
546            adapalene 0.1 %+ benzoyl peroxide 2.5 %   

                                  vector         dosage  \
0    [-5.7047486, -1.1721812, 1.3178241]         [25.0]   
1     [-5.513812, -0.9735408, 1.1201787]         [50.0]   
2    [-6.151596, -1.3261145, 0.82413894]      [50.0, 5]   
3    [-6.151596, -1.3261145, 0.82413894]      [5.0, 50]   
4    [-6.151596, -1.3261145, 0.82413894]             []   
..                                   ...            ...   
542    [3.845325, 1.7525554, -1.6686797]    [150.0, 75]   
543    [3.391115, 1.6387248, -1.7444034]  [75.0, 150.0]   
544      [4.05685, 1.7666304, -2.056936]     [75.0, 75]   
545  [-6.041723, -1.7156223, -0.3165637]     [75.0, 75]   
546  [-6.041723, -1.7156223, -0.3165637]     [0.1, 2.5]   

                                            SumVectors  \
0                                [0.025, 0.025, 0.025]   
1                                   [0.05, 0.05, 0.05]   
2                                [0.055, 0.055, 0.055]   
3                                [0.055, 0.055, 0.055]   
4                                                  0.0   
..                                                 ...   
542  [0.22499999999999998, 0.22499999999999998, 0.2...   
543  [0.22499999999999998, 0.22499999999999998, 0.2...   
544                                 [0.15, 0.15, 0.15]   
545                                 [0.15, 0.15, 0.15]   
546                           [0.0026, 0.0026, 0.0026]   

                                          final_vector  
0    [-5.679748630523681, -1.147181248664856, 1.342...  
1    [-5.463812065124512, -0.9235407829284668, 1.17...  
2    [-6.096596069335938, -1.2711145353317261, 0.87...  
3    [-6.096596069335938, -1.2711145353317261, 0.87...  
4                  [-6.151596, -1.3261145, 0.82413894]  
..                                                 ...  
542  [4.070324993133545, 1.9775553703308106, -1.443...  
543  [3.616114950180054, 1.8637248039245606, -1.519...  
544  [4.2068499565124515, 1.9166304111480712, -1.90...  
545  [-5.891722774505615, -1.5656223058700562, -0.1...  
546  [-6.039122774505615, -1.7130223058700562, -0.3...  

[547 rows x 6 columns]

In [197]:
## implementing the quasi random sampling to select some anchor points.
total_samples = len(new_df)
sample_size = len(new_df)/3
period  = int(total_samples/sample_size)


In [198]:
anchors = []
anchor_indexes=[]
for i in range(0,len(new_df)+1,period):
    try:
        anchors.append(new_df['Medicine_Name'][i])
        anchor_indexes.append(i)
    except:
        pass

In [199]:
Vectors = new_df['final_vector'].values

In [200]:
from numpy import dot
from numpy.linalg import norm

# cos_sim = dot(a, b)/(norm(a)*norm(b))
anchor_euc_scores = {}
for i in range(0, len(anchor_indexes)):
    print(str(i) + " done!")
    current_index = anchor_indexes[i]
    current_point = Vectors[current_index]
    euc_sim_scores = []
    for j in range(0, len(words_list)):
        
        other_point = Vectors[j]

        # Check for zero norms
        norm_current = norm(current_point)
        norm_other = norm(other_point)

        if norm_current == 0 or norm_other == 0:
            euc_sim = 0  # or any other value you choose
        else:
            euc_sim = 1 / (1 + np.linalg.norm(norm_current - norm_other))

        euc_sim_scores.append([j, euc_sim * 100000])

    euc_sim_scores = sorted(euc_sim_scores , key=lambda k: [k[1], k[0]], reverse=True)
    anchor_euc_scores[anchor_indexes[i]] = euc_sim_scores[0:500]


0 done!
1 done!
2 done!
3 done!
4 done!
5 done!
6 done!
7 done!
8 done!
9 done!
10 done!
11 done!
12 done!
13 done!
14 done!
15 done!
16 done!
17 done!
18 done!
19 done!
20 done!
21 done!
22 done!
23 done!
24 done!
25 done!
26 done!
27 done!
28 done!
29 done!
30 done!
31 done!
32 done!
33 done!
34 done!
35 done!
36 done!
37 done!
38 done!
39 done!
40 done!
41 done!
42 done!
43 done!
44 done!
45 done!
46 done!
47 done!
48 done!
49 done!
50 done!
51 done!
52 done!
53 done!
54 done!
55 done!
56 done!
57 done!
58 done!
59 done!
60 done!
61 done!
62 done!
63 done!
64 done!
65 done!
66 done!
67 done!
68 done!
69 done!
70 done!
71 done!
72 done!
73 done!
74 done!
75 done!
76 done!
77 done!
78 done!
79 done!
80 done!
81 done!
82 done!
83 done!
84 done!
85 done!
86 done!
87 done!
88 done!
89 done!
90 done!
91 done!
92 done!
93 done!
94 done!
95 done!
96 done!
97 done!
98 done!
99 done!
100 done!
101 done!
102 done!
103 done!
104 done!
105 done!
106 done!
107 done!
108 done!
109 done!
110 done!


In [201]:
with open(r'C:\Users\ayush\OneDrive\Documents\polyglot\PolyGlot\data\preturbing\meta-main.txt', 'w') as the_file:
    the_file.write('0\n')
    for i in range(0, len(anchors)):
        the_file.write(str(anchor_indexes[i]) + ' ' + anchors[i] + '\n')

with open(r'C:\Users\ayush\OneDrive\Documents\polyglot\PolyGlot\data\preturbing\full_data', 'w',encoding="utf-8") as the_file:
    for i in range(0, len(new_df['Medicine_Name'])):
        word = new_df['Medicine_Name'][i]
        if word in anchors:
            is_anchor = 1
        else:
            is_anchor = 0
        if word == 'Synonym'or word == 'Vitamin D3':
            pass
        else:
            
            the_file.write(word +' ----> '+new_df['Salts'][i] +'\n')
            try:
              the_file.write(str(Vectors[i][0]) + ' ' + str(Vectors[i][1]) + ' ' + str(Vectors[i][2]) + ' ' + str(is_anchor) + ' \n')
            except:
              the_file.write(str(Vectors[i]) +' ' + str(is_anchor) + ' \n')

folder_path  = r"C:\Users\ayush\OneDrive\Documents\polyglot\PolyGlot\data\preturbing"
for anchor_index in anchor_indexes:
    filename = os.path.join(folder_path, str(anchor_index) + '.txt')
    with open(filename, 'w') as the_file:
        for score in anchor_euc_scores[anchor_index]:
            # note that score is of the form: [index, cosine]
            the_file.write(str(score[0]) + ', ' + str(score[1]) + '\n')